# **Notebook des villes majeures dans le monde impactées par des séismes d'une magnitude > 6.1 entre 2000 et 2024**

données :
séismes : https://earthquake.usgs.gov/earthquakes/search/

lien : https://earthquake.usgs.gov/earthquakes/map/?extent=-77.54265,-47.46094&extent=74.40147,380.03906&range=search&timeZone=utc&search=%7B%22name%22:%22Search%20Results%22,%22params%22:%7B%22starttime%22:%222023-11-19%2000:00:00%22,%22endtime%22:%222024-11-26%2023:59:59%22,%22minmagnitude%22:6.1,%22orderby%22:%22time%22%7D%7D



villes : https://hub.arcgis.com/datasets/schools-BE::world-cities/explore

lien :https://hub.arcgis.com/datasets/schools-BE::world-cities/explore?location=10.596177%2C-0.934039%2C2.32



In [1]:
!pip install mapclassify

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.1/59.1 kB 2.2 MB/s eta 0:00:00


In [97]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point
import folium
from folium import plugins
from google.colab import files

cities_url = "https://raw.githubusercontent.com/krapoutch/Earthquake_hazards/main/World_Cities/World_Cities.shp"
seismes_url = "https://raw.githubusercontent.com/krapoutch/Earthquake_hazards/main/query_2000.csv"



In [98]:
gdf = gpd.read_file(seismes_url)
gdf.head()

time latitude longitude   depth  mag magType  nst  gap  \
0  2024-11-26T13:47:03.761Z  37.0718  136.4671      10  6.1     mww  101   35   
1  2024-11-17T12:16:29.918Z  29.0501  131.3955       8  6.1     mww  130   32   
2  2024-11-15T05:28:29.617Z  -4.7021  153.3201  51.891  6.6     mww   50   67   
3  2024-11-10T16:49:50.382Z  19.8116  -77.0391      14  6.8     mww   87   25   
4  2024-11-08T11:37:57.944Z  -46.786  -76.1693      10  6.2     mww   48  195   

    dmin   rms  ...                   updated  \
0   1.49  1.05  ...  2024-11-26T15:06:10.633Z   
1  2.583  0.91  ...  2024-11-18T12:27:00.670Z   
2   1.26  1.35  ...  2024-11-17T09:55:24.266Z   
3   0.61  0.89  ...  2024-11-17T01:36:29.648Z   
4  2.471  1.06  ...  2024-11-09T11:44:48.478Z   

                                    place        type horizontalError  \
0                35 km NW of Hakui, Japan  earthquake            6.12   
1            155 km SSE of Koshima, Japan  earthquake             3.1   
2  123 km ESE of Kokopo, Papua New Guinea  earthquake            8.85   
3       40 km SSW of Bartolomé Masó, Cuba  earthquake            2.61   
4           278 km WNW of Cochrane, Chile  earthquake            7.94   

  depthError magError magNst    status locationSource magSource  
0      1.824    0.053     34  reviewed             us        us  
1      1.823    0.041     56  reviewed             us        us  
2      7.797    0.061     26  reviewed             us        us  
3      1.655    0.032     94  reviewed             us        us  
4      1.928    0.038     68  reviewed             us        us  

[5 rows x 22 columns]

In [99]:
# Cree la geometrie des points "seismes" en fonction de la latitude et la longitude
geometry = [Point(xy) for xy in zip(gdf['longitude'], gdf['latitude'])]

# Cree un nouveau GeoDataFrame avec la geometries des points "seismes"
gdf_points = gpd.GeoDataFrame(gdf, geometry=geometry, crs="EPSG:4326")

# Reproject le GeoDataFrame en format EPSG:3857
gdf_points = gdf_points.to_crs("EPSG:3857")

In [84]:
cities_shp = gpd.read_file(cities_url)
cities_shp.head()

FID  OBJECTID             CITY_NAME GMI_ADMIN          ADMIN_NAME  \
0    1         1                Cuiaba   BRA-MGR         Mato Grosso   
1    2         2              Brasilia   BRA-DFD    Distrito Federal   
2    3         3               Goiania   BRA-GOI               Goias   
3    4         4          Campo Grande   BRA-MGD  Mato Grosso do Sul   
4    5         5  Pedro Juan Caballero   PRY-AMM             Amambay   

  FIPS_CNTRY CNTRY_NAME                           STATUS      POP  POP_RANK  \
0         BR     Brazil               Provincial capital   540814         3   
1         BR     Brazil  National and provincial capital  2481272         2   
2         BR     Brazil               Provincial capital  1297154         2   
3         BR     Brazil               Provincial capital   776242         3   
4         PA   Paraguay               Provincial capital        0         0   

                POP_CLASS  PORT_ID  LABEL_FLAG         POP_SOURCE  \
0      500,000 to 999,999        0           0  UN_Data_2010_2020   
1  1,000,000 to 4,999,999        0           0  UN_Data_2010_2020   
2  1,000,000 to 4,999,999        0           0  UN_Data_2010_2020   
3      500,000 to 999,999        0           0  UN_Data_2010_2020   
4                    None        0           0               None   

                            geometry  
0   POINT (-6244244.606 -1760180.18)  
1  POINT (-5331952.879 -1780660.511)  
2  POINT (-5483041.697 -1889069.697)  
3  POINT (-6079824.826 -2326534.952)  
4  POINT (-6205838.719 -2575640.106)

In [6]:
cities_shp.crs # Verification du systeme de coordonnees

<Projected CRS: EPSG:3857>
Name: WGS 84 / Pseudo-Mercator
Axis Info [cartesian]:
- X[east]: Easting (metre)
- Y[north]: Northing (metre)
Area of Use:
- name: World between 85.06°S and 85.06°N.
- bounds: (-180.0, -85.06, 180.0, 85.06)
Coordinate Operation:
- name: Popular Visualisation Pseudo-Mercator
- method: Popular Visualisation Pseudo Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [92]:
gdf_points.crs # Verification du systeme de coordonnees

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [104]:
seismes_buffer = gdf_points.buffer(100000) # Creation d'un buffer de 100km autour des seismes

In [105]:
# Utilisation du spatial join pour identifier les villes dans le buffer seismes
cities_in_buffer = gpd.sjoin(cities_shp, gpd.GeoDataFrame(geometry=seismes_buffer, crs=cities_shp.crs), how="inner", predicate="intersects")

In [106]:
cities_in_buffer.shape

(791, 16)

In [49]:
# Obtenir les nomes des villes dans le buffer
cities_in_buffer_names = set(cities_in_buffer['CITY_NAME'])

# Filtrer les villes dans le buffer depuis le datasat cities_shp
cities_shp_filtered = cities_shp[~cities_shp['CITY_NAME'].isin(cities_in_buffer_names)]

gdf_points["time"] = gdf_points["time"].str[:4] # Modifier le format du champ "time" afin de ne garder que les 4 premiers caracteres correspondant a l'annee du seisme

In [63]:
# Certaines villes ont une valeur de 0 dans le champ "POP" (Population) ==> Valeur de 0 dans le fichier d'entree

m = cities_shp_filtered.explore(tooltip = ["CITY_NAME", "POP"], tooltip_kwds = {"aliases": ["Ville", "Population"]}, popup = ["CITY_NAME", "POP"], popup_kwds = {"aliases": ["Ville", "Population"]}, name = "Villes Majeures", color = "Blue")

gdf_points.explore(m=m, tooltip = ["time", "place", "depth", "mag"], tooltip_kwds = {"aliases": ["Annee", "Lieu", "Profondeur", "Magnitude"]}, popup = ["time", "place", "depth", "mag"], popup_kwds = {"aliases": ["Annee", "Lieu", "Profondeur", "Magnitude"]}, name = "Seismes", color = "Black")

cities_in_buffer.explore(m=m, tooltip = ["CITY_NAME", "POP"], tooltip_kwds = {"aliases": ["Ville", "Population"]}, popup = ["CITY_NAME", "POP"], popup_kwds = {"aliases": ["Ville", "Population"]}, name = "Villes Majeures Impactees", color = "Red")

minimap = plugins.MiniMap()
m.add_child(minimap)

folium.LayerControl(position='bottomright').add_to(m)

In [67]:
m

In [68]:
m.save("Earthquake_hazards_LBNRG.html")
files.download("Earthquake_hazards_LBNRG.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>